In [1]:
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt
import plotly.figure_factory as ff
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot
from plotly.subplots import make_subplots
from datetime import date
from yahooquery import Ticker

In [2]:
""" start and end date of entire time series """
start_date = pd.to_datetime('1920-1-1')
end_date = date.today()
""" SP500 """
# we use yahooquery.Ticker to read yahoo finance data; function argument is ticker symbol
sp500 = Ticker('^GSPC')
df = sp500.history(start=start_date, end=end_date, interval='1d')
df.index = df.index.normalize() # remove time portion of datetime
df = df.pct_change()['adjclose'].dropna().to_frame() # work with daily percentage change

""" time horizon (in days) and confidence level for computing VaR/ES """
time_period = 252 
p = 5 # p := VaR(1-p)

# initialize new dataframe for storing results
df_res = pd.DataFrame(columns=['start', 'end', 'VaR', 'ES', 'returns'])
# start: starting date, end: ending date of each period we will compute VaR/ES
df_res['start'] = df.iloc[:-time_period].index
df_res['end'] = df.iloc[time_period:].index

# computes VaR and ES
for i, row in df_res.iterrows(): # iterate through each row of df_res
    # subset percent changes in a given period
    returns = df.loc[row['start']:row['end']].values.flatten()
    df_res.at[i, 'returns'] = returns
    # computes VaR (p^th-quantile)
    returns_var = np.percentile(returns, q=p)
    df_res.at[i, 'VaR'] = -returns_var
    # compute ES
    df_res.at[i, 'ES'] = -np.mean(returns[returns<returns_var])

# read start and end date of past US recessions; for highlighting recession periods in plot
recession_periods = pd.read_csv('../data/recession_periods_NBER.csv', skiprows=lambda x: x in range(1,20)) # use dates classified by NBER
peaks = recession_periods['Peak'].tolist()
troughs = recession_periods['Trough'].tolist()
# set up parameters for plotting historical recessions from 1930 to 2009 + covid19 recession
recession_shades = [dict(type="rect",xref="x",yref="paper",
                    x0=t0,y0=0, x1=t1, y1=1,
                    fillcolor="LightSalmon",opacity=0.4,layer="below",line_width=0) for t0, t1 in zip(peaks, troughs)]
recession_shades.append(dict(type="rect",xref="x",yref="paper",
                        x0="2020-2-20",y0=0,x1=date.today(),y1=1, 
                        fillcolor="LightSalmon",opacity=0.4,layer="below",line_width=0))

In [3]:
# visualize value of historical realized VaR, ES and their ratio
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(name='VaR', x=df_res['start'], y=df_res['VaR'], hovertemplate=' %{y:.2%}'), secondary_y=False)
fig.add_trace(go.Scatter(name='ES', x=df_res['start'], y=df_res['ES'], hovertemplate=' %{y:.2%}'), secondary_y=False)
fig.add_trace(go.Scatter(name='VaR : ES', x=df_res['start'], y=df_res['VaR']/df_res['ES'], hovertemplate=' %{y:.2f}'), secondary_y=True)
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(
    title='VaR and ES w.r.t daily percent change',
    hovermode='x unified', 
    autosize=False,
    width=1200,
    height=450,
    margin=dict(l=20,r=20,b=20,t=20,pad=4),
    yaxis=dict(tickformat='.0%', rangemode = 'tozero'),
    xaxis=dict(tickformat='%d %b %Y'),
    # all recession periods will be highlighted
    shapes = recession_shades,
    legend=dict(y=1.12)
)
fig.show()

In [4]:
# this is a preview of the dataframe that will be used to construct time-series histogram plot
# length of time-horizon is given by time_period
df_res[::-1][::time_period][::-1]

start        end         VaR         ES  \
31    1928-02-16 1929-02-19   0.0166197  0.0234451   
283   1929-02-19 1930-02-24   0.0367692  0.0638343   
535   1930-02-24 1931-02-26   0.0335338  0.0430348   
787   1931-02-26 1932-02-26   0.0412285  0.0533595   
1039  1932-02-26 1933-03-01   0.0525484  0.0652106   
...          ...        ...         ...        ...   
21955 2015-06-04 2016-06-03   0.0171105   0.024091   
22207 2016-06-03 2017-06-05  0.00735456  0.0144673   
22459 2017-06-05 2018-06-05   0.0129539  0.0214007   
22711 2018-06-05 2019-06-06   0.0184805  0.0242393   
22963 2019-06-06 2020-06-05   0.0299787  0.0527204   

                                                 returns  
31     [-0.002873519434293592, -0.017867403984236807,...  
283    [-0.00041001349455060954, 0.00861365869770947,...  
535    [-0.010471194167507636, 0.009259218767502908, ...  
787    [0.011129703426912219, -0.0077049746318433865,...  
1039   [-0.0011976321467036533, -0.005995226597130032...  
...                                                  ...  
21955  [-0.008623167576889856, -0.0014361829335245435...  
22207  [-0.002911814656949452, 0.004897281193053882, ...  
22459  [-0.001217665183814387, -0.0027790399654609166...  
22711  [0.0007025929724704394, 0.008567392465728796, ...  
22963  [0.006135586748687638, 0.01049769746289475, 0....  

[92 rows x 5 columns]

In [20]:
# plot time series of histogram of daily percent change
df_hist = df_res[::-1][::252][::-1]
fig=go.Figure()
""" specify the time period we want to plot """
t0=pd.to_datetime('1995-1-1'); t1=pd.to_datetime('2010-6-5')
df_hist = df_hist[(df_hist['start'] < t1) & (df_hist['start'] > t0)]

for row in df_hist.itertuples():
    a0=np.histogram(row.returns, bins=20, density=False)[0].tolist()
    a0=np.repeat(a0,2).tolist()
    a0.insert(0,0)
    a0.pop()
    a1=np.histogram(row.returns, bins=20, density=False)[1].tolist()
    a1=np.repeat(a1,2)
    # mark periods that go through recession as orange
    if any([((pd.to_datetime(t0) < row.start) & (row.start < pd.to_datetime(t1))) | 
            ((pd.to_datetime(t0) < row.end) & (row.end < pd.to_datetime(t1))) for t0, t1 in zip(peaks, troughs)]):
        color = 'orange'
    else:
        color = 'blue'
    fig.add_traces(go.Scatter3d(x=[row.Index]*len(a1), y=a1, z=a0, 
                                mode='lines', line={'color':color},
                                hovertemplate='%{y:.2%}, %{z}',
                                name=str(row.start.date())+ ' - ' + str(row.end.date())))
# add VaR and ES
fig.add_traces(go.Scatter3d(x=df_hist.index, y=-df_hist['VaR'], z=[0]*len(df_hist), 
                                mode='lines', line={'color':'purple'},
                                hovertemplate='%{y:.2%}', name='VaR'
                                ))
fig.add_traces(go.Scatter3d(x=df_hist.index, y=-df_hist['ES'], z=[0]*len(df_hist), 
                                mode='lines', line={'color':'red'},
                                hovertemplate='%{y:.2%}', name='ES'
                                ))
# aspectratio: change the ratio of x,y,z axis's length in display
fig.update_layout(width=1100,height=500,margin=dict(l=0,r=0,b=20,t=20,pad=4),
                scene=dict(aspectratio=dict(x=2,y=1, z=0.6), aspectmode = 'manual', 
                xaxis=dict(tickvals=df_hist.index, ticktext=df_hist['start'].apply(lambda x: pd.to_datetime(x).year), title=dict(text='')),
                yaxis=dict(range=[-0.1,0.1], mirror=True, tickformat='%{.2%}', title=dict(text='daily percentage')),
                zaxis=dict(showticklabels=False, title=dict(text='frequency')),
                camera=dict(eye=dict(x=1.25,y=-1.8,z=0.2))))
fig.show()


In [6]:
# VaR/ES in recession vs. non-recession period statistics: histogram
# risk256.com

# count exceedance
# test of conditional independence 
# number of exceedances given some level of market volatility; market condition (recession vs. non-recession)
# co-integration of VaR and ES